In [1]:
import sys, os, platform, torch

In [2]:
!git clone https://github.com/olimpiadnik/dla_hw3.git
%cd dla_hw3
!ls

Cloning into 'dla_hw3'...
remote: Enumerating objects: 262, done.
remote: Counting objects: 100% (262/262), done.
remote: Compressing objects: 100% (197/197), done.
remote: Total 262 (delta 63), reused 206 (delta 42), pack-reused 0 (from 0)
Receiving objects: 100% (262/262), 3.21 MiB | 28.82 MiB/s, done.
Resolving deltas: 100% (63/63), done.
/content/dla_hw3
CITATION.cff  LICENSE	 requirements.txt  scripts  synthesize.py
inference.py  README.md  samples	   src	    train.py


In [3]:
!pip install -q -r requirements.txt

!pip install -q espnet espnet_model_zoo g2p_en nltk

import nltk
nltk.download('averaged_perceptron_tagger_eng')

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.6/57.6 kB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.4/70.4 kB 7.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.2/78.2 kB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.1/70.1 kB 6.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.1/70.1 kB 6.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.5/70.5 kB 7.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 68.2/68.2 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.6/67.6 kB 6.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.2/67.2 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 65.8/65.8 kB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 65.5/65.5 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

[nltk_data] Downloading package averaged_perceptron_tagger_eng to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger_eng.zip.


True

In [5]:
from pathlib import Path
import yadisk
import zipfile

DATA_ZIP_URL = "https://disk.360.yandex.ru/d/Mzh9T9OEZKSsww"
DATA_DIR = Path("grade_dataset")
DATA_DIR.mkdir(exist_ok=True)
DATA_ZIP_NAME = "grade_dataset.zip"

y = yadisk.YaDisk()

zip_path = DATA_DIR / DATA_ZIP_NAME

print("Downloading dataset from Yandex Disk...")

with open(zip_path, "wb") as f:
    y.download_public(DATA_ZIP_URL, f)

print("Unzipping...")
with zipfile.ZipFile(zip_path, "r") as zf:
    zf.extractall(DATA_DIR)

print("Done. Files are in:", DATA_DIR.resolve())

Unzipping...
Done. Files are in: /content/dla_hw3/grade_dataset


In [6]:
CHECKPOINT_URL = "https://disk.yandex.ru/d/Y13vly-deqTA6Q"  # ссылка на hifigan_hifigan_baseline_ep50.zip
CHECKPOINT_ZIP_NAME = "hifigan_hifigan_baseline_ep50.zip"

!python scripts/download_checkpoints.py \
  --url "{CHECKPOINT_URL}" \
  --out-dir . \
  --zip-name "{CHECKPOINT_ZIP_NAME}"

!echo "Saved dir:"
!ls -R saved

[download_checkpoints] Downloading from https://disk.yandex.ru/d/Y13vly-deqTA6Q to hifigan_hifigan_baseline_ep50.zip ...
[download_checkpoints] Unzipping hifigan_hifigan_baseline_ep50.zip into . ...
[download_checkpoints] Done.
Saved dir:
saved:
hifigan_baseline

saved/hifigan_baseline:
checkpoint-epoch15.pth	checkpoint-epoch35.pth	git_commit.txt
checkpoint-epoch20.pth	checkpoint-epoch40.pth	git_diff.patch
checkpoint-epoch27.pth	checkpoint-epoch50.pth	info.log
checkpoint-epoch30.pth	config.yaml		model_best.pth


In [8]:
#пробуем ресинтез

In [7]:
!python synthesize.py \
    --checkpoint-path saved/hifigan_baseline/model_best.pth \
    --mode resynthesize \
    --input-audio-dir grade_dataset/test_data/gt_audio \
    --output-dir samples/grade_resynth \
    --device auto

Using device: cuda
Loading model from checkpoint: saved/hifigan_baseline/model_best.pth
/usr/local/lib/python3.12/dist-packages/torch/nn/utils/weight_norm.py:28: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")
Found 5 files. Writing resynth audio to samples/grade_resynth, sr=22050
[resynthesize] bernstein.wav -> bernstein.wav
[resynthesize] dla.wav -> dla.wav
[resynthesize] pupin.wav -> pupin.wav
[resynthesize] shostakovich.wav -> shostakovich.wav
[resynthesize] termen.wav -> termen.wav


In [9]:
import IPython.display as ipd

print("GT Shostakovich:") # можно выбрать любую другую пару аудио
ipd.display(ipd.Audio("grade_dataset/test_data/gt_audio/shostakovich.wav", rate=22050))

print("Resynth Shostakovich (HiFi-GAN):")
ipd.display(ipd.Audio("samples/grade_resynth/shostakovich.wav", rate=22050))

GT Shostakovich:


Resynth Shostakovich (HiFi-GAN):


In [14]:
#ттс в колабе к сожалению не работает из-за несовместипости еспнет с питоном 3.12
# Я приведу сравнение сгенерированных мною ранее версий.
# Протестировать ттс можно локально или в kaggle

In [16]:
from IPython.display import Audio, display
print("Deep Learning in Audio course at HSE University offers an exciting and challenging exploration of cutting-edge techniques in audio processing, from speech recognition to music analysis. With complex homeworks that push students to apply theory to real-world problems, it provides a hands-on, rigorous learning experience that is both demanding and rewarding.")
print("Ground truth DLA:")
display(Audio("grade_dataset/test_data/gt_audio/dla.wav"))
print("Synthesized DLA:")
display(Audio("samples/mos/mos_01_hse_course.wav"))



Deep Learning in Audio course at HSE University offers an exciting and challenging exploration of cutting-edge techniques in audio processing, from speech recognition to music analysis. With complex homeworks that push students to apply theory to real-world problems, it provides a hands-on, rigorous learning experience that is both demanding and rewarding.
Ground truth DLA:


Synthesized DLA:
